In [11]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [12]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if "workding_dir" not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/papers/rapget-translation


In [13]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/papers/rapget-translation/.env


True

In [14]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"
max_new_tokens = int(os.getenv("MAX_NEW_TOKENS", 2048))

print(
    model_name,
    adapter_name_or_path,
    load_in_4bit,
    data_path,
    results_path,
    use_english_datasets,
    max_new_tokens,
)

Qwen/Qwen2-7B-Instruct None False datasets/mac/mac.tsv results/mac-results_rpp_with_mnt_2048.csv False 2048


In [15]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, peft, torchaudio, torchvision, trl
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tok

In [16]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

MPS is available


In [17]:
df_openai = load_openai_training_data(
    data_path, openai_data_path="logs/openai-training-sample.jsonl"
)
df_openai

loading existing data from: logs/openai-training-sample.jsonl


messages
0  [{'role': 'system', 'content': 'Marv is a fact...
1  [{'role': 'system', 'content': 'Marv is a fact...
2  [{'role': 'system', 'content': 'Marv is a fact...

In [18]:
print_row_details(df_openai, range(len(df_openai)))

--------------------------------------------------
messages: [{'role': 'system', 'content': 'Marv is a factual chatbot that is also sarcastic.'}, {'role': 'user', 'content': "What's the capital of France?"}, {'role': 'assistant', 'content': "Paris, as if everyone doesn't know that already."}]
--------------------------------------------------
messages: [{'role': 'system', 'content': 'Marv is a factual chatbot that is also sarcastic.'}, {'role': 'user', 'content': "Who wrote 'Romeo and Juliet'?"}, {'role': 'assistant', 'content': 'Oh, just some guy named William Shakespeare. Ever heard of him?'}]
--------------------------------------------------
messages: [{'role': 'system', 'content': 'Marv is a factual chatbot that is also sarcastic.'}, {'role': 'user', 'content': 'How far is the Moon from Earth?'}, {'role': 'assistant', 'content': 'Around 384,400 kilometers. Give or take a few, like that really matters.'}]


In [22]:
from openai import OpenAI


def start_fine_tuning(epochs, mini=False):
    client = OpenAI()
    model = "gpt-4o-mini-2024-07-18" if mini else "gpt-4o-2024-08-06"

    jobs = []
    for epoch in epochs:
        job = client.fine_tuning.jobs.create(
            training_file="file-IokPHn4YWcniXL4wGnK4xVmn",
            model=model,
            seed=1046194933,
            hyperparameters={
                "n_epochs": epoch,
                "batch_size": 18,
                "learning_rate_multiplier": 1.8,
            },
            integrations=[
                {
                    "type": "wandb",
                    "wandb": {
                        "project": "OpenAI",
                        "name": f"{model}-{epoch}",
                    },
                },
            ],
        )
        jobs.append(job)

    return jobs

In [23]:
start_fine_tuning([1, 2])

RateLimitError: Error code: 429 - {'error': {'message': "This fine-tune request has been rate-limited. Your organization has reached the maximum of 5 fine-tuning requests per day for the model 'gpt-4o-2024-08-06'.", 'type': 'invalid_request_error', 'param': None, 'code': 'daily_rate_limit_exceeded'}}

In [24]:
fine_tuned_models = [
    "ft:gpt-4o-2024-08-06:mastercard::A0krlVBL",
]

In [25]:
from llm_toolkit.eval_openai import evaluate_model_with_num_shots

loading env vars from: /Users/inflaton/code/engd/papers/rapget-translation/.env
Adding /Users/inflaton/code/engd/papers/rapget-translation to sys.path
Qwen/Qwen2-7B-Instruct datasets/mac/mac.tsv results/mac-results_rpp_with_mnt_2048.csv 2048


In [26]:
for i, model in enumerate(fine_tuned_models):
    epoch = i + 1
    evaluate_model_with_num_shots(
        model,
        data_path,
        results_path="results/mac-results_few_shots_openai.csv",
        range_num_shots=[0],
        max_new_tokens=max_new_tokens,
        result_column_name=f"gpt-4o/epochs-{epoch:02d}",
    )

Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A0krlVBL
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
*** Evaluating with num_shots: 0


100%|██████████| 1133/1133 [19:12<00:00,  1.02s/it]


gpt-4o/epochs-01 metrics: {'meteor': 0.37829977579665147, 'sacrebleu': {'score': 11.961183004083166, 'counts': [12783, 4604, 2130, 1067], 'totals': [29124, 27991, 26875, 25764], 'precisions': [43.89163576431809, 16.448144046300598, 7.925581395348837, 4.141437664958858], 'bp': 0.9640596438285618, 'sys_len': 29124, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11961183004083172, 'precisions': [0.4389163576431809, 0.16448144046300597, 0.07925581395348837, 0.04141437664958857], 'brevity_penalty': 0.9640596438285618, 'length_ratio': 0.9646902947996026, 'translation_length': 29124, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.42429274225313846, 'rouge2': 0.17523641258245923, 'rougeL': 0.369425658597467, 'rougeLsum': 0.369423462411946}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}


In [28]:
start_fine_tuning([2, 3])

[FineTuningJob(id='ftjob-3w97Tp1zZWD4XlytggsgPgGc', created_at=1724854813, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=2, batch_size=18, learning_rate_multiplier=1.8), model='gpt-4o-2024-08-06', object='fine_tuning.job', organization_id='org-RXHVnD8cqPvqTPdXgZ5rQdl3', result_files=[], seed=1046194933, status='validating_files', trained_tokens=None, training_file='file-IokPHn4YWcniXL4wGnK4xVmn', validation_file=None, estimated_finish=None, integrations=[FineTuningJobWandbIntegrationObject(type='wandb', wandb=FineTuningJobWandbIntegration(project='OpenAI', entity=None, name=None, tags=None, run_id='ftjob-3w97Tp1zZWD4XlytggsgPgGc'))], user_provided_suffix=None),
 FineTuningJob(id='ftjob-ZOMJygL3RnVl0hYOeWpF2byf', created_at=1724854815, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=3, batch_size=18, learning_rate_multi

In [29]:
start_fine_tuning([4, 5])

[FineTuningJob(id='ftjob-MkT46Oelgt1DLmG0sQQO9WFY', created_at=1724881432, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=4, batch_size=18, learning_rate_multiplier=1.8), model='gpt-4o-2024-08-06', object='fine_tuning.job', organization_id='org-RXHVnD8cqPvqTPdXgZ5rQdl3', result_files=[], seed=1046194933, status='validating_files', trained_tokens=None, training_file='file-IokPHn4YWcniXL4wGnK4xVmn', validation_file=None, estimated_finish=None, integrations=[FineTuningJobWandbIntegrationObject(type='wandb', wandb=FineTuningJobWandbIntegration(project='OpenAI', entity=None, name=None, tags=None, run_id='ftjob-MkT46Oelgt1DLmG0sQQO9WFY'))], user_provided_suffix=None),
 FineTuningJob(id='ftjob-iVLC48wzUyqHW7QLoPEVZ23e', created_at=1724881433, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=5, batch_size=18, learning_rate_multi

In [31]:
start_fine_tuning([6])

[FineTuningJob(id='ftjob-oEa3YrzGmFS9SWxsMFY4KK4i', created_at=1724903446, error=Error(code=None, message=None, param=None), fine_tuned_model=None, finished_at=None, hyperparameters=Hyperparameters(n_epochs=6, batch_size=18, learning_rate_multiplier=1.8), model='gpt-4o-2024-08-06', object='fine_tuning.job', organization_id='org-RXHVnD8cqPvqTPdXgZ5rQdl3', result_files=[], seed=1046194933, status='validating_files', trained_tokens=None, training_file='file-IokPHn4YWcniXL4wGnK4xVmn', validation_file=None, estimated_finish=None, integrations=[FineTuningJobWandbIntegrationObject(type='wandb', wandb=FineTuningJobWandbIntegration(project='OpenAI', entity=None, name=None, tags=None, run_id='ftjob-oEa3YrzGmFS9SWxsMFY4KK4i'))], user_provided_suffix=None)]

In [32]:
fine_tuned_models = [
    "ft:gpt-4o-2024-08-06:mastercard::A0krlVBL",
    "ft:gpt-4o-2024-08-06:mastercard::A1E8HfT2",
    "ft:gpt-4o-2024-08-06:mastercard::A1EEMdkp",
    "ft:gpt-4o-2024-08-06:mastercard::A1LIBJeg",
    "ft:gpt-4o-2024-08-06:mastercard::A1LKnnlI",
]

In [33]:
for i, model in enumerate(fine_tuned_models):
    epoch = i + 1
    if epoch < 2:
        continue

    evaluate_model_with_num_shots(
        model,
        data_path,
        results_path="results/mac-results_few_shots_openai.csv",
        range_num_shots=[0],
        max_new_tokens=max_new_tokens,
        result_column_name=f"gpt-4o/epochs-{epoch:02d}",
    )

Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A1E8HfT2
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
*** Evaluating with num_shots: 0


100%|██████████| 1133/1133 [17:26<00:00,  1.08it/s]


gpt-4o/epochs-02 metrics: {'meteor': 0.378362442260616, 'sacrebleu': {'score': 11.94987840396735, 'counts': [12801, 4612, 2127, 1061], 'totals': [29101, 27968, 26852, 25740], 'precisions': [43.98817910037456, 16.490274599542335, 7.9211976761507525, 4.121989121989122], 'bp': 0.9632701331199107, 'sys_len': 29101, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11949878403967351, 'precisions': [0.4398817910037456, 0.16490274599542334, 0.07921197676150753, 0.04121989121989122], 'brevity_penalty': 0.9632701331199107, 'length_ratio': 0.9639284531301755, 'translation_length': 29101, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4244959919113983, 'rouge2': 0.17487441168118406, 'rougeL': 0.36961992190392845, 'rougeLsum': 0.3696134312327403}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A1EEMdkp
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    }

 43%|████▎     | 491/1133 [4:02:55<5:17:37, 29.68s/it]


KeyboardInterrupt: 

In [34]:
for i, model in enumerate(fine_tuned_models):
    epoch = i + 1
    if epoch < 3:
        continue

    evaluate_model_with_num_shots(
        model,
        data_path,
        results_path="results/mac-results_few_shots_openai.csv",
        range_num_shots=[0],
        max_new_tokens=max_new_tokens,
        result_column_name=f"gpt-4o/epochs-{epoch:02d}",
    )

Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A1EEMdkp
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
*** Evaluating with num_shots: 0


100%|██████████| 1133/1133 [18:51<00:00,  1.00it/s] 


gpt-4o/epochs-03 metrics: {'meteor': 0.37969689267707335, 'sacrebleu': {'score': 12.039126826084276, 'counts': [12800, 4627, 2152, 1077], 'totals': [29117, 27984, 26868, 25756], 'precisions': [43.9605728612151, 16.53444825614637, 8.009528063123419, 4.181549930113372], 'bp': 0.9638194215435517, 'sys_len': 29117, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.1203912682608427, 'precisions': [0.43960572861215097, 0.1653444825614637, 0.08009528063123418, 0.041815499301133714], 'brevity_penalty': 0.9638194215435517, 'length_ratio': 0.9644584299436899, 'translation_length': 29117, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4253565511807691, 'rouge2': 0.1762509031111424, 'rougeL': 0.3709362250350436, 'rougeLsum': 0.37090080700005995}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A1LIBJeg
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })

 92%|█████████▏| 1045/1133 [41:47<03:31,  2.40s/it]   


KeyboardInterrupt: 

In [37]:
for i, model in enumerate(fine_tuned_models):
    epoch = i + 1
    if epoch < 4:
        continue

    evaluate_model_with_num_shots(
        model,
        data_path,
        results_path="results/mac-results_few_shots_openai.csv",
        range_num_shots=[0],
        max_new_tokens=max_new_tokens,
        result_column_name=f"gpt-4o/epochs-{epoch:02d}",
    )

Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A1LIBJeg
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})
--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
*** Evaluating with num_shots: 0


100%|██████████| 1133/1133 [18:37<00:00,  1.01it/s]


gpt-4o/epochs-04 metrics: {'meteor': 0.3784063502724225, 'sacrebleu': {'score': 11.971696060849887, 'counts': [12785, 4606, 2132, 1069], 'totals': [29104, 27971, 26855, 25743], 'precisions': [43.92866959868059, 16.467055164277287, 7.938931297709924, 4.152585168783747], 'bp': 0.9633731468442895, 'sys_len': 29104, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.11971696060849878, 'precisions': [0.4392866959868059, 0.16467055164277286, 0.07938931297709924, 0.04152585168783747], 'brevity_penalty': 0.9633731468442893, 'length_ratio': 0.9640278237827095, 'translation_length': 29104, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4238707558842832, 'rouge2': 0.17481350068875362, 'rougeL': 0.3695909612883631, 'rougeLsum': 0.36945188893013925}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
Evaluating model: ft:gpt-4o-2024-08-06:mastercard::A1LKnnlI
loading train/test data files
DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    

100%|██████████| 1133/1133 [19:22<00:00,  1.03s/it]


gpt-4o/epochs-05 metrics: {'meteor': 0.3797983554067647, 'sacrebleu': {'score': 12.064338049153614, 'counts': [12791, 4641, 2157, 1081], 'totals': [29111, 27978, 26862, 25750], 'precisions': [43.93871732334856, 16.58803345485739, 8.029930757203484, 4.1980582524271846], 'bp': 0.9636134724514155, 'sys_len': 29111, 'ref_len': 30190}, 'bleu_scores': {'bleu': 0.12064338049153608, 'precisions': [0.43938717323348564, 0.16588033454857387, 0.08029930757203485, 0.041980582524271844], 'brevity_penalty': 0.9636134724514155, 'length_ratio': 0.9642596886386221, 'translation_length': 29111, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4248543304997294, 'rouge2': 0.1768290761907465, 'rougeL': 0.370949573624763, 'rougeLsum': 0.370875336303769}, 'accuracy': 0.00088261253309797, 'correct_ids': [77]}
